# 模型拟合与评价 API

(PopModel)=

## mas.model.PopModel

```{py:class} mas.model.PopModel(mod, data=None)

```

群体模型。对其可以进行模型拟合与模拟等操作。

此处的“群体模型”一般指代的是用于拟合群体数据的非线性混合效应模型（继承自 `Module` 的模型）。

**参数：**

- **mod** _(`AnyModule`)_：模型。
- **data** _(`polars.DataFrame | pandas.DataFrame | EventTable`, optional)_：需要被模型拟合的数据集。默认值为 `None`。

### data

```{py:property} data

```

获取将被模型拟合的数据集。

**类型：**

`DataFrame`

### inits

```{py:property} inits

```

获取模型参数及其初值。

**类型：**

`PopParams`


(PopModel-fit)=

### fit()

```{py:method} fit(estimation=FOCEi, cov=True) -> FitResult

```

拟合模型。

**参数：**

- **estimation** _(`AnyEstimationSettings | Sequence[AnyEstimationSettings]`, optional)_：参数估计的算法及其[相关设置](optimizer-settings)。当前支持的算法包括 `FOCEi` （first-order conditional estimation with interaction）与 `FO`（first-order estimation）。若传入一个序列（`Sequence`）则将根据传入顺序依次以对应的算法估计参数。默认值为 `FOCEi`。
- **cov** _(`bool`, optional)_：是否计算协方差矩阵。默认值为 `True`。

**返回值：**

包含参数估计值的模型拟合结果。

**返回类型：**

`FitResult`


**示例：**

使用 FOCEi 算法拟合华法林 PK 模型：


In [1]:
from mas.model import *
from mas.datasets import warfarin
import polars as pl


class WarfarinPk(EvOneCmtLinear):
    def __init__(self):
        super().__init__()
        self.tv_cl = theta(0.134, bounds=(0, None))
        self.tv_v = theta(7.81, bounds=(0, None))
        self.tv_ka = theta(0.571, bounds=(0, None))
        self.tv_alag = theta(0.823, bounds=(0, None))
        self.eta_cl = omega(0.049)
        self.eta_v = omega(0.0802)
        self.eta_ka = omega(0.047)
        self.eta_alag = omega(0.156)
        self.eps_prop = sigma(0.0104)
        self.eps_add = sigma(0.554)

    def pred(self):
        cl = self.tv_cl * exp(self.eta_cl)
        v = self.tv_v * exp(self.eta_v)
        ka = self.tv_ka * exp(self.eta_ka)
        alag = self.tv_alag * exp(self.eta_alag)
        pred_res = self.pred_physio(cl=cl, v=v, ka=ka, alag1=alag, s2=v)
        ipred = pred_res.F
        y = ipred * (1 + self.eps_prop) + self.eps_add
        return y


data = warfarin.filter(pl.col("DVID") != 2)
model = PopModel(data=data, mod=WarfarinPk)
fit_res = model.fit(FOCEi(print=10))

➡️ Since build cache already exists, skip compile
✈️ First Order Conditional Estimation
Using BFGS...
* maxiter = 9999
* xtol = 1e-06
* ftol = 1e-06
* lower_bounds = 
* upper_bounds = 
* log_level = 0
* print = 10
* print_type = 0
* verbose = 1
* p_small = 0.1
* rel_step_size = 0.001

#0    ofv: 347.7917575
x: 1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  
Gradients: -10.5092 -8.33744 -96.9252 30.7996 -27.5129 17.5438 -33.1212 -11.5115 43.1845 122.184 

Funcalls: 8
#1    ofv: 252.9367067
x: 1.5161e-01  1.4094e-01  5.7596e-01  -5.1245e-02 2.3511e-01  1.3849e-02  2.6265e-01  1.5653e-01  -1.1206e-01 -5.0000e-01 
Gradients: 58.5006 19.4823 -12.6546 0.438415 -20.9679 14.0305 -33.114 -4.19792 7.4639 42.0374 

Funcalls: 17
#11   ofv: 219.1455368
x: 6.6127e-02  1.1409e-01  1.1175e+00  1.3436e-01  3.6191e-01  -1.8678e-01 1.6618e+00  -3.4381e-02 -4.8288e-02 -1.0445e+00 
Gradients: -12.2346 -8.00718 1.12182 2.07945 -0.31765

In [2]:
fit_res

Estimation Summary                                                              

────────────────────────────────────────────────────────────────────────────────
    OFV       Converged      Total     Compilation   Estimation   Covariance 
                           Iterations      Time         Time         Time    
────────────────────────────────────────────────────────────────────────────────
     217.997       True ✅           24    0:00:00.2   0:00:01.25   0:00:01.66
────────────────────────────────────────────────────────────────────────────────


Parameter Estimation                                                            

────────────────────────────────────────────────────────────────────────────────
 Parameter     Estimate   Shrinkage(%)    RSE(%)   
────────────────────────────────────────────────────────────────────────────────
Theta                                              
       tv_cl        0.132                     5.218
        tv_v        7.978                     4.075
       tv_ka        1.354                    31.919
     tv_alag        0.824                    19.057
Omega(SD)                                          
      eta_cl        0.289        0.000       14.186
       eta_v        0.220        3.993       13.348
      eta_ka        0.835       50.453       19.177
    eta_alag        0.394       59.245       28.372
Sigma(SD)                                          
    eps_prop        0.086       14.952       14.144
     eps_add        0.259       15.635       23.639
────────────────────────────────────────────────────────────────────────────────

(optimizer-settings)=

#### 支持的算法设置

```{list-table}
:header-rows: 1

* - 设置
  - 功能
* - `print: int = 1`
  - 每 `print` 次迭代打印一次迭代历史详情。
* - `verbose: Literal["silent", "info", "debug", "trace"] = "info"`
  - 输出详尽等级。若为 `"info"` 则正常打印迭代历史与其他输出信息。若为 `"silent"` 则不进行任何打印。
* - `minimize_method: Literal["nm", "powell", "bobyqa", "lbfgs", "newuoa", "bfgs"] = "lbfgs"`
  - 最小化方法。
* - `maxiter: int = 9999`
  - 最大迭代次数。
* - `xtol: float = 1e-6`
  - 相对参数收敛界值。
* - `ftol: float = 1e-6`
  - 相对目标函数收敛界值。
* - `cov_method: Literal["r", "s", "rs"] = "rs"`
  - 协方差估算方法。
* - `map_minimizer: Literal["nm", "powell", "bobyqa", "lbfgs", "newuoa", "bfgs"] = "lbfgs"`
  - eta 参数最小化方法（仅适用于 FOCEi 算法）。
* - `cov_minimizer: Literal["nm", "powell", "bobyqa", "lbfgs", "newuoa", "bfgs"] = "lbfgs"`
  - 协方差最小化方法（仅适用于 FOCEi 算法）。
* - `extra: dict[str, str | int | float | bool] = dict()`
  - 各最小化方法[额外设置选项](extra-settings)。
```

(extra-settings)=

#### 支持的各最小化方法额外设置选项

##### lbfgs

```{list-table}
:header-rows: 1

* - 设置
  - 功能
* - `lbfgs_rank: int = 20`
  - 用于方向计算（direction calculation）的迭代次数。
* - `use_approx_eigen_scaling: bool = False`
  - 使用近似特征值（approximate eigenvalue scaling）。
* - `ls_interp_type: int = 2`
  - 用于近似目标函数的多项式的次数。
* - `min_ls_step_size: float = 1e-9`
  - 最小线搜索（line search）步长。
* - `gtol: float = 1e-10`
  - 相对梯度收敛界值。
* - `num_method: int = 1`
  - 数值微分（numerical differentiation）方法。 若为 `0` 则使用中心（central）差分；若为 `1` 则使用前向（forward）差分；若为 `2` 则使用 Ridders 方法。
* - `rel_step: float = 1e-3`
  - 数值微分方法相对步长（relative step size）。
```

##### BObyQA 与 NEWUOA

```{list-table}
:header-rows: 1

* - 设置
  - 功能
* - `initial_trust_region_radius: float = 0.01`
  - 初始信赖域（trust region）大小。
* - `final_trust_region_radius: float = 1e-6`
  - 最终信赖域大小。
```

##### Nelder-Mead

```{list-table}
:header-rows: 1

* - 设置
  - 功能
* - `alpha: float = 1.0`
  - 反射（reflection）系数。
* - `beta: float = 0.5`
  - 扩展（contraction）系数
* - `gamma: float = 2.0`
  - 收缩（expansion）参数。
* - `delta: float = 0.5`
  - 回退（shrinkage）系数。
* - `adaptive: bool = True`
  - 是否使用自适应（adaptive）参数。
```


(PopModel-simulate)=

### simulate()

```{py:method} simulate(data=None, param=None, seed=1234) -> SimulationResult

```

运行模型模拟。

**参数：**

- **data** _(`DataFrame | EventTable`, optional)_：用于模拟的数据集。若为 `None` 则使用模型将要拟合的数据集（即在创建 {ref}`PopModel <PopModel>` 时指定的 `data`）。支持使用 {ref}`EventTable <EventTable>`。默认值为 `None`。
- **params** _(`AnyPopParams`, optional)_：用于模拟的参数值。若为 `None` 则使用模型中的参数初值。默认值为 `None`。
- **seed** _(`int`, optional)_：随机种子。默认值为 `1234`。

**返回值：**

包含模拟数据集的模拟结果。

**返回类型：**

`SimulationResult`


**示例：**

模拟华法林的 PK 场景


In [3]:
sim_res = model.simulate(data)
sim_res.output

shape: (288, 22)
┌─────┬───────┬───────┬──────┬───┬──────────┬──────────┬───────────┬───────────┐
│ ID  ┆ TIME  ┆ AMT   ┆ DV   ┆ … ┆ ipred    ┆ ka       ┆ v         ┆ y         │
│ --- ┆ ---   ┆ ---   ┆ ---  ┆   ┆ ---      ┆ ---      ┆ ---       ┆ ---       │
│ i64 ┆ f64   ┆ f64   ┆ f64  ┆   ┆ f64      ┆ f64      ┆ f64       ┆ f64       │
╞═════╪═══════╪═══════╪══════╪═══╪══════════╪══════════╪═══════════╪═══════════╡
│ 0   ┆ 0.0   ┆ 100.0 ┆ null ┆ … ┆ 0.0      ┆ 0.764926 ┆ 7.788145  ┆ -0.380376 │
│ 0   ┆ 0.5   ┆ null  ┆ 0.0  ┆ … ┆ 0.0      ┆ 0.764926 ┆ 7.788145  ┆ -0.23897  │
│ 0   ┆ 1.0   ┆ null  ┆ 1.9  ┆ … ┆ 0.0      ┆ 0.764926 ┆ 7.788145  ┆ -0.439278 │
│ 0   ┆ 2.0   ┆ null  ┆ 3.3  ┆ … ┆ 6.661621 ┆ 0.764926 ┆ 7.788145  ┆ 6.363483  │
│ 0   ┆ 3.0   ┆ null  ┆ 6.6  ┆ … ┆ 9.724606 ┆ 0.764926 ┆ 7.788145  ┆ 8.120754  │
│ …   ┆ …     ┆ …     ┆ …    ┆ … ┆ …        ┆ …        ┆ …         ┆ …         │
│ 32  ┆ 36.0  ┆ null  ┆ 7.7  ┆ … ┆ 6.383142 ┆ 0.43094  ┆ 10.676541 ┆ 5.126728  │
│ 32  ┆ 48.0  ┆ null  ┆ 6.9  ┆ … ┆ 5.701332 ┆ 0.43094  ┆ 10.676541 ┆ 5.605446  │
│ 32  ┆ 72.0  ┆ null  ┆ 4.4  ┆ … ┆ 4.548411 ┆ 0.43094  ┆ 10.676541 ┆ 4.553091  │
│ 32  ┆ 96.0  ┆ null  ┆ 3.5  ┆ … ┆ 3.628633 ┆ 0.43094  ┆ 10.676541 ┆ 3.950745  │
│ 32  ┆ 120.0 ┆ null  ┆ 2.5  ┆ … ┆ 2.894852 ┆ 0.43094  ┆ 10.676541 ┆ 3.605601  │
└─────┴───────┴───────┴──────┴───┴──────────┴──────────┴───────────┴───────────┘

(PopModel-to-nonmem)=

### to_nonmem()

```{py:method} to_nonmem(dir, control_filename=None, data_filename=None) -> None

```

将模型翻译为 NONMEM 控制文件代码。

**参数：**

- **dir** _(`PathLike`)_：翻译结果输出路径
- **control_filename** _(`str`, optional)_：输出的控制文件文件名。若为 `None` 则采用 `模型类名.mod` 的命名形式。默认值为 `None`。
- **data_filename** _(`str`, optional)_：输出的数据集文件文件名。若为 `None` 则采用 `模型类名.csv` 的命名形式。默认值为 `None`。


## mas.model.EstimationResult

```{py:class} mas.model.EstimationResult

```

模型参数估计结果。

### ofv

```{py:property} ofv

```

当前参数估计结果对应的目标函数值。

**类型：**

`float`

### estimates

```{py:property} estimates

```

模型参数估计结果。

**类型：**

`PopParams`

### converged

```{py:property} converged

```

目标函数最小化过程中参数估计是否收敛。

**类型：**

`bool`

### n_iter

```{py:property} n_iter

```

迭代次数。

**类型：**

`int`

### est_time

```{py:property} est_time

```

参数估计耗时。

**类型：**

`timedelta`


(FitResult)=

## mas.model.FitResult

```{py:class} mas.model.FitResult

```

模型拟合结果。

### ofv

```{py:property} ofv
:noindex:
```

所有最小化过程结束后参数估计结果对应的目标函数值。

**类型：**

`float`

### estimates

```{py:property} estimates
:noindex:
```

所有最小化过程结束后得到的参数估计值。

**类型：**

`PopParams`

### converged

```{py:property} converged
:noindex:
```

所有最小化过程结束后参数估计是否收敛。

**类型：**

`bool`

### n_iter

```{py:property} n_iter
:noindex:
```

所有最小化过程的总迭代次数。

**类型：**

`int`

### inits

```{py:property} inits
:noindex:
```

模型参数初值。

**类型：**

`PopParams`

### est_sequence

```{py:property} est_sequence
:noindex:
```

各最小化过程的参数估计结果。

**类型：**

`list[EstimationResult]`

### iterations

```{py:property} iterations
:noindex:
```

各次迭代的参数估计结果。

**类型：**

`list[IterationResults]`

### compile_time

```{py:property} compile_time
:noindex:
```

模型编译耗时。

**类型：**

`timedelta`

### est_time

```{py:property} est_time
:noindex:
```

参数估计耗时。

**类型：**

`timedelta`

### cov_time

```{py:property} cov_time
:noindex:
```

协方差估计耗时。

**类型：**

`timedelta | None`

### elapsed_time

```{py:property} elapsed_time
:noindex:
```

模型拟合所花费的总耗时。

**类型：**

`timedelta`

### output

```{py:property} output
:noindex:
```

包含观测值、群体预测值、个体预测值与个体参数值（以最后一次最小化过程的结果为准）的数据集。

**类型：**

`DataFrame`

### covariance

```{py:property} covariance
:noindex:
```

协方差估计结果。

**类型：**

`CovResult`

(FitResult-summary)=

### summary()

```{py:method} summary() -> None
:noindex:
```

打印模型拟合结果摘要。

### compute()

```{py:method} compute(residuals=None) -> DataFrame
:noindex:
```

计算群体预测值（population predictions）、个体预测值（individual predictions）与残差（residuals）。

**参数：**

- **residuals** _(`list[Literal["CWRES", "WRES", "CWRESI", "WRESI", "CIWRES", "IWRES", "CIWRESI", "IWRESI"]]`, optional)_：需要计算的残差类型。如果为 `None` 则跳过残差计算。默认值为 `None`。

**返回值：**

包含指定计算内容的 `DataFrame`。

**返回类型：**

`DataFrame`

### ebe()

```{py:method} ebe() -> DataFrame
:noindex:
```

计算 eta 参数的经验贝叶斯估计。

**返回值：**

包含各个个体经验贝叶斯估计值的 `DataFrame`。

**返回类型：**

`DataFrame`

### eta_shr()

```{py:method} eta_shr(method="sd", ebv=False) -> DataFrame
:noindex:
```

计算 eta 参数的收缩量。

:::{admonition} eta 参数收缩量公式
:name: eta-shr-formula

若为标准差形式，计算公式如下：

$$
shr = [1 - \frac{SD(eta(j))}{\sqrt{omega(j, j)}}] \times 100\%
$$

若为方差形式，计算公式如下：

$$
shr = [1 - \frac{Var(eta(j))}{\sqrt{omega(j, j)}}] \times 100\%
$$

其中，eta(j) 为第 j 个 eta 参数的个体经验贝叶斯估计值。
:::

**参数：**

- **method** _(`Literal["sd", "var"]`, optional)_：计算收缩量的方法。使用标准差形式（`"sd"`）或方差形式（`"var"`）。默认值为 `"sd"`。计算公式可见：[eta 参数收缩量公式](eta-shr-formula)。
- **ebv** _(`bool`, optional)_：是否计算平均经验贝叶斯方差。默认值为 `False`。

**返回值：**

eta 参数收缩量的数据框。

**返回类型：**

`DataFrame`

**示例：**


In [4]:
fit_res.eta_shr("sd")

shape: (1, 4)
┌────────────┬──────────┬─────────┬──────────┐
│ eta_cl     ┆ eta_v    ┆ eta_ka  ┆ eta_alag │
│ ---        ┆ ---      ┆ ---     ┆ ---      │
│ f64        ┆ f64      ┆ f64     ┆ f64      │
╞════════════╪══════════╪═════════╪══════════╡
│ 1.0000e-10 ┆ 0.039934 ┆ 0.50453 ┆ 0.592446 │
└────────────┴──────────┴─────────┴──────────┘

### eps_shr()

```{py:method} eps_shr(method="sd") -> DataFrame
:noindex:
```

计算 eps 参数的收缩量。

:::{admonition} eps 参数收缩量公式
:name: eps-shr-formula

若为标准差形式，计算公式如下：

$$
shr = [1 - SD(IWRES)] \times 100\%
$$

若为方差形式，计算公式如下：

$$
shr = [1 - Var(IWRES)] \times 100\%
$$

其中，IWRES 为个体加权残差（individual weighted residual）。
:::

**参数：**

- **method** _(`Literal["sd", "var"]`, optional)_：计算收缩量的方法。使用标准差形式（`"sd"`）或方差形式（`"var"`）。默认值为 `"sd"`。计算公式可见：[eps 参数收缩量公式](eps-shr-formula)。

**返回值：**

eps 参数收缩量的数据框。

**返回类型：**

`DataFrame`

(FitResult-plot-gof)=

### plot_gof()

```{py:method} plot_gof(self, filter=None, idv_name=None, dv_name=None, wres="CWRES", iwres="CIWRES") -> Plot

```

绘制模型拟合优度图（goodness of fit）。

**参数：**

- **filter** _(`Expr`, optional)_: 筛选条件，对于部分数据进行 gof 绘制。默认值为 `None`。
- **idv_name** _(`str`, optional)_：因变量名。若为 `None`，则自动推断。默认值为 `None`。
- **dv_name** _(`str`, optional)_：自变量名。若为 `None`，则自动推断。默认值为 `None`。
- **wres** _(`Literal["CWRES", "CWRESI", "WRES", "WRESI"]`, optional)_：需要计算的加权残差类型（weighted residuals）。默认值为 `"CWRES"`。
- **iwres** _(`Literal["CIWRES", "CIWRESI", "IWRES", "IWRESI"]`, optional)_：需要计算的个体加权残差类型（individual weighted residual）。默认值为 `"CIWRES"`。

**示例：**


In [5]:
fit_res.plot_gof()

(FitResult-plot-predictions)=

### plot_predictions()

```{py:method} plot_predictions(self, filter=None, idv_name=None, dv_name=None, wres="CWRES", iwres="CIWRES") -> Plot

```

绘制个体拟合图（个体预测值/群体预测值 vs. 实测值）。

**参数：**

- **filter** _(`Expr`, optional)_: 筛选条件，对于部分数据进行个体拟合图绘制。默认值为 `None`。
- **idv_name** _(`str`, optional)_：因变量名。若为 `None`，则自动推断。默认值为 `None`。
- **dv_name** _(`str`, optional)_：自变量名。若为 `None`，则自动推断。默认值为 `None`。
- **wres** _(`Literal["CWRES", "CWRESI", "WRES", "WRESI"]`, optional)_：需要计算的加权残差类型（weighted residuals）。默认值为 `"CWRES"`。
- **iwres** _(`Literal["CIWRES", "CIWRESI", "IWRES", "IWRESI"]`, optional)_：需要计算的个体加权残差类型（individual weighted residual）。默认值为 `"CIWRES"`。

**示例：**


In [6]:
fit_res.plot_predictions(filter=pl.col("SEX") == 0)

(FitResult-plot-iterations)=

### plot_iterations()

```{py:method} plot_iterations(self) -> Plot

```

绘制迭代历史图（目标函数值与各模型参数估计值在迭代间的变动情况）。

**示例：**


In [7]:
fit_res.plot_iterations().with_x_grid(visible=True).with_y_grid(visible=True)

(FitResult-vpc)=

### vpc()

```{py:method} vpc(n_sample=1000, seed=1234, ci_level=0.95, percentile_level=0.95, auto_bin=True, min_points_in_each_bin=10, linear_interpolation=True, *, dv_name=None, idv_name=None) -> VpcResult

```

运行模型可视化预测检验（visual predictive check）。

**参数：**

- **n_sample** _(`int`, optional)_：抽样次数。默认值为 `1000`。
- **seed** _(`int`, optional)_：随机种子号。默认值为 `1234`。
- **ci_level** _(`float`, optional)_：模拟数据百分位数的置信水平。默认值为 `0.95`。
- **percentile_level** _(`float`, optional)_：模拟数据与实测值的百分位数水平。默认值为 `0.95`，即取 2.5% 与 97.5% 分位数。
- **auto_bin** _(`bool | int | tuple[int, int]`, optional)_：分箱（binning）方法。默认值为 `True`。具体方法如下：
  - 若为 `True`，则使用自动分箱方法。
  - 若为 `False`，则视每一个观测时间点为一个分箱。
  - 若为 `int`，则视分箱数目为 `int`，将基于此数目计算每个箱体的范围。
  - 若为 `tuple[int, int]`，则视箱体的范围为 `tuple[int, int]`，将基于此范围计算最终的分箱数目。
- **min_points_in_each_bin** _(`int`, optional)_：每个分箱中需包含的最少观测点数目。默认值为 `10`。
- **linear_interpolation** _(`bool`, optional)_：是否进行线性化。默认值为 `True`。
- **idv_name** _(`str`, optional)_：因变量名。若为 `None`，则自动推断。默认值为 `None`。
- **dv_name** _(`str`, optional)_：自变量名。若为 `None`，则自动推断。默认值为 `None`。

**返回值：**

包含 VPC 图、置信区间数据、模拟数据等相关内容的检验结果。

**返回类型：**

`VpcResult`

**示例：**


In [13]:
vpc_res = fit_res.vpc(linear_interpolation=False)
vpc_res.plot()

[VPC] Preparing data...
[VPC] Running simulation...
Running Auto-bin...
Bin search ended, result is 10
Auto-bin completed, finally use 10 bins.


(FitResult-bootstrap)=

### bootstrap()

```{py:method} bootstrap(n_sample=1000, seed=1234, level=0.95) -> BootstrapResult

```

运行自举法（bootstrap）。

**参数：**

- **n_sample** _(`int`, optional)_：抽样次数。默认值为 `1000`。
- **seed** _(`int`, optional)_：随机种子号。默认值为 `1234`。
- **level** _(`float`, optional)_：参数估计值的置信水平。默认值为 `0.95`。

**返回值：**

包含估算成功率与抽样数据等相关内容的检验结果。

**返回类型：**

`BootstrapResult`


(FitResult-scm)=

### scm()

```{py:method} scm(config) -> ScmResultCollection

```

利用 SCM 法（stepwise covariate modeling）进行协变量筛选。

**参数：**

- **config** _(`ScmConfig | typing.Callable[[], ScmConfig]`)_：SCM 配置。可详见 {ref}`ScmConfig <ScmConfig>`。

**返回值：**

SCM 运行结果汇总。

**返回类型：**

`ScmResultCollection`
